## Very naive and straightforward text categorization

In [ ]:
import string
import collections
import glob
import codecs
import numpy as np
import scipy as sp
from scipy.sparse import lil_matrix

In [ ]:
translator = str.maketrans("","", string.punctuation)
dirs = glob.glob('20news-bydate-train/*')

In [ ]:
train_set = []
train_labels = []
total_counts = collections.Counter()
for directory in dirs:
    filenames = glob.glob(directory + '/*')
    print(directory, len(filenames))
    for filename in filenames:
        with codecs.open(filename, 'r', 'latin1') as f:
            lines = f.readlines()
            lines_proc = [y for x in lines for y in x.strip().lower().translate(translator).split()]
            count = collections.Counter(lines_proc)
            total_counts += count
            train_set.append(count)
            train_labels.append(directory)

In [ ]:
vocab_counts = {w: c for w, c in total_counts.items() if c > 9}
vocab = {w: i for i,w in enumerate(sorted(vocab_counts.keys()))}

In [ ]:
len(vocab)

In [ ]:
X = lil_matrix((len(train_set), len(vocab)))
for i_doc, doc in enumerate(train_set):
    for w,c in doc.items():
        if w in vocab:
            X[i_doc, vocab[w]] = c

In [ ]:
labels_array = sorted(collections.Counter(train_labels).keys())
labels_dict = {l: i for i, l in enumerate(labels_array)}
y = np.array([labels_dict[x] for x in train_labels])

In [ ]:
y.shape, X.shape

In [ ]:
X

In [ ]:
from sklearn.naive_bayes import BernoulliNB, MultinomialNB

In [ ]:
model = MultinomialNB()
model.fit(X, y)

In [ ]:
model.coef_.shape

In [ ]:
model.score(X, y)

In [ ]:
model = BernoulliNB()
model.fit(X, y)
model.score(X, y)

In [ ]:
test_set = []
test_labels = []
for directory in glob.glob('20news-bydate-test/*'):
    filenames = glob.glob(directory + '/*')
    print(directory, len(filenames))
    for filename in filenames:
        with codecs.open(filename, 'r', 'latin1') as f:
            lines = f.readlines()
            lines_proc = [y for x in lines for y in x.strip().lower().translate(translator).split() if y in vocab]
            count = collections.Counter(lines_proc)
            test_set.append(count)
            test_labels.append(directory)

In [ ]:
X_test = lil_matrix((len(test_set), len(vocab)))
for i_doc, doc in enumerate(test_set):
    for w,c in doc.items():
        if w in vocab:
            X[i_doc, vocab[w]] = c

In [ ]:
y_test = np.array([labels_dict['20news-bydate-train/' + x.split('/')[1]] for x in test_labels])

In [ ]:
def test_model(model, name=None):
    if not name is None:
        print(name)
    model.fit(X, y)
    print("Train set: %.5f\tTest set: %.5f" % (model.score(X, y), model.score(X_test, y_test)) )

In [ ]:
test_model(MultinomialNB(), 'MultinomialNB')
test_model(BernoulliNB(), 'BernoulliNB')

Oh my God! Nothing works! What do we do?..